# Document Intelligence with Markdown

In this notebook we will experiment with Document Intelligence and its Markdown output. We will try reading documents and experiment whether Document Intelligence can manage advanced actions, such as reading multi-page tables. 


### Notes:
- Getting 404 when calling document_intelligence_client.begin_analyze_document
  - Help in finding solution - [ResourceNotFoundError (404) with DocumentIntelligenceClient · Issue #33312 · Azure/azure-sdk-for-python · GitHub](https://github.com/Azure/azure-sdk-for-python/issues/33312)
  - **Solution:** Make sure that resource is in supported region - [Document layout analysis - Document Intelligence (formerly Form Recognizer) - Azure AI services | Microsoft Learn](https://learn.microsoft.com/en-us/azure/ai-services/document-intelligence/concept-layout?view=doc-intel-4.0.0)

- Not all pages are analyzed (sample_data/2_ai_facts.pdf)
  - For some reason only first two pages are analyzed. This is not an issue with sample_data/2_ai_facts.docx
  - Same problem is observed in Document Intelligence Studio
  - **Solution:** Change Document Intelligence resource pricing tier from F0 -> S0


### Python Imports


In [57]:
%load_ext autoreload
%autoreload 2


import sys
sys.path.append('..\\code')


import os
from dotenv import load_dotenv
load_dotenv()

from IPython.display import display, Markdown, HTML
from PIL import Image
from doc_utils import *


def show_img(img_path, width = None):
    if width is not None:
        display(HTML(f'<img src="{img_path}" width={width}>'))
    else:
        display(Image.open(img_path))


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


### Make sure we have the OpenAI Models information

We will need the GPT-4-Turbo and GPT-4-Vision models for this notebook.

When running the below cell, the values should reflect the OpenAI reource you have created in the `.env` file.

In [58]:
model_info = {
        'AZURE_OPENAI_RESOURCE': os.environ.get('AZURE_OPENAI_RESOURCE'),
        'AZURE_OPENAI_KEY': os.environ.get('AZURE_OPENAI_KEY'),
        'AZURE_OPENAI_MODEL_VISION': os.environ.get('AZURE_OPENAI_MODEL_VISION'),
        'AZURE_OPENAI_MODEL': os.environ.get('AZURE_OPENAI_MODEL'),
}

### Experimenting with Document Intelligence

First make sure to install the right version of Document Intelligence

In [59]:
## This version corresponds to API Version 2024-02-29-preview
## Visit: https://learn.microsoft.com/en-us/python/api/overview/azure/ai-documentintelligence-readme?view=azure-python-preview

%pip install azure-ai-documentintelligence>=1.0.0b2

Note: you may need to restart the kernel to use updated packages.


Defining a helper function

In [60]:
from azure.core.credentials import AzureKeyCredential
from azure.ai.documentintelligence import DocumentIntelligenceClient
from azure.ai.documentintelligence.models import AnalyzeResult
from azure.ai.documentintelligence.models import AnalyzeDocumentRequest, ContentFormat

DI_ENDPOINT = os.environ["DI_ENDPOINT"]
DI_KEY = os.environ["DI_KEY"]

def analyze_document(path):
    document_intelligence_client = DocumentIntelligenceClient(endpoint=DI_ENDPOINT, credential=AzureKeyCredential(DI_KEY))

    with open(path, "rb") as f:
        poller = document_intelligence_client.begin_analyze_document(
            "prebuilt-layout", analyze_request=f, output_content_format=ContentFormat.MARKDOWN, content_type="application/octet-stream"
        )
    result: AnalyzeResult = poller.result()
    
    return result



In [61]:
import fitz  # PyMuPDF

# Create a sub-directory to store the outputs
work_dir = "sample_data/hdgdemo/pdf_outputs"
os.makedirs(work_dir, exist_ok=True)

# Load a sample PDF document

def read_pdf(pdf_doc):
    doc = fitz.open(pdf_doc)
    print(f"PDF File {os.path.basename(pdf_doc)} has {len(doc)} pages.")
    return doc

def nb_extract_pages_as_png_files(doc):
    png_files = []
    for page in doc:
        page_num = page.number
        img_path = f"{work_dir}/page_{page_num}.png"
        page_pix = page.get_pixmap(dpi=300)
        page_pix.save(img_path)
        print(f"Page {page_num} saved as {img_path}")
        png_files.append(img_path)
    
    return png_files


pdf_doc = "sample_data/hdgdemo/Niche_Master_Blain_Keating.pdf"
doc = read_pdf(pdf_doc)
png_files = nb_extract_pages_as_png_files(doc)  


PDF File Niche_Master_Blain_Keating.pdf has 50 pages.
Page 0 saved as sample_data/hdgdemo/pdf_outputs/page_0.png
Page 1 saved as sample_data/hdgdemo/pdf_outputs/page_1.png
Page 2 saved as sample_data/hdgdemo/pdf_outputs/page_2.png
Page 3 saved as sample_data/hdgdemo/pdf_outputs/page_3.png
Page 4 saved as sample_data/hdgdemo/pdf_outputs/page_4.png
Page 5 saved as sample_data/hdgdemo/pdf_outputs/page_5.png
Page 6 saved as sample_data/hdgdemo/pdf_outputs/page_6.png
Page 7 saved as sample_data/hdgdemo/pdf_outputs/page_7.png
Page 8 saved as sample_data/hdgdemo/pdf_outputs/page_8.png
Page 9 saved as sample_data/hdgdemo/pdf_outputs/page_9.png
Page 10 saved as sample_data/hdgdemo/pdf_outputs/page_10.png
Page 11 saved as sample_data/hdgdemo/pdf_outputs/page_11.png
Page 12 saved as sample_data/hdgdemo/pdf_outputs/page_12.png
Page 13 saved as sample_data/hdgdemo/pdf_outputs/page_13.png
Page 14 saved as sample_data/hdgdemo/pdf_outputs/page_14.png
Page 15 saved as sample_data/hdgdemo/pdf_outputs/pa

#### Reading in Sample Documents

In [ ]:
path = r"sample_data/hdgdemo/Niche_Master_Blain_Keating.pdf"
niche_pdf_result = analyze_document(path)
Markdown(niche_pdf_result['content'])

### Figures

For the same document, check if any Figures are detected for the PDF version

In [28]:
niche_pdf_result.keys()

dict_keys(['apiVersion', 'modelId', 'stringIndexType', 'content', 'pages', 'tables', 'paragraphs', 'styles', 'contentFormat', 'sections', 'figures'])

In [63]:
niche_pdf_result['figures']

[{'id': '1.1', 'boundingRegions': [{'pageNumber': 1, 'polygon': [1.1103, 2.2464, 7.3922, 2.2486, 7.3928, 3.703, 1.1106, 3.7004]}], 'spans': [{'offset': 0, 'length': 45}], 'elements': ['/paragraphs/0']}]

In [65]:
niche_pdf_result['pages']

[{'pageNumber': 1, 'angle': 0.3262624144554138, 'width': 8.5, 'height': 11, 'unit': 'inch', 'words': [{'content': 'ClearAlpha®', 'polygon': [3.3125, 2.2078, 7.2936, 2.2228, 7.2936, 3.0005, 3.3149, 2.9417], 'confidence': 0.626, 'span': {'offset': 10, 'length': 11}}, {'content': 'Technologies', 'polygon': [3.3057, 2.9908, 7.1553, 3.025, 7.1553, 3.7257, 3.3028, 3.635], 'confidence': 0.992, 'span': {'offset': 22, 'length': 12}}, {'content': 'NICHE', 'polygon': [2.3099, 4.284, 3.1058, 4.2884, 3.105, 4.5532, 2.3091, 4.5509], 'confidence': 0.992, 'span': {'offset': 48, 'length': 5}}, {'content': 'PLUS', 'polygon': [3.1754, 4.2885, 3.78, 4.2894, 3.779, 4.5572, 3.1746, 4.5537], 'confidence': 0.992, 'span': {'offset': 54, 'length': 4}}, {'content': 'MASTER', 'polygon': [3.8453, 4.2895, 4.8761, 4.2967, 4.8754, 4.5617, 3.8442, 4.5577], 'confidence': 0.994, 'span': {'offset': 59, 'length': 6}}, {'content': 'FUND', 'polygon': [4.9326, 4.2972, 5.5851, 4.2988, 5.5844, 4.5617, 4.932, 4.5617], 'confiden

In [ ]:
from PIL import Image

def get_dpi(image):
    try:
        dpi = image.info['dpi']
        print("DPI", dpi)
    except KeyError:
        dpi = (300, 300)
    return dpi

def polygon_to_bbox(polygon):
    xs = polygon[::2]  # Extract all x coordinates
    ys = polygon[1::2]  # Extract all y coordinates
    left = min(xs)
    top = min(ys)
    right = max(xs)
    bottom = max(ys)
    return (left, top, right, bottom)


def inches_to_pixels(inches, dpi):
    dpi_x, dpi_y = dpi
    return [int(inches[i] * dpi_x if i % 2 == 0 else inches[i] * dpi_y) for i in range(len(inches))]

polygon = [2.7496, 2.5964, 7.1241, 2.597, 7.1249, 5.0656, 2.7505, 5.0645]


def extract_figure(image_path, polygon):
    bbox_in_inches = polygon_to_bbox(polygon)

    # Load the image
    image = Image.open(image_path)

    filename = os.path.splitext(os.path.basename(image_path))[0].strip()
    extension = os.path.splitext(os.path.basename(image_path))[1].strip()
    crop_name = os.path.join(os.path.dirname(image_path), f"{filename}_{generate_uuid_from_string(str(polygon))}{extension}")
    print(f"Cropped image will be saved under name: {crop_name}")

    # Get DPI from the image
    dpi = get_dpi(image)

    # Convert the bounding box to pixels using the image's DPI
    bbox_in_pixels = inches_to_pixels(bbox_in_inches, dpi)
    print("bbox_in_pixels", bbox_in_pixels)

    # Crop the image
    cropped_image = image.crop(bbox_in_pixels)
    cropped_image.save(crop_name)  
    show_img(crop_name, 400)

for bounding in niche_pdf_result['figures']:
    polygon = bounding['boundingRegions'][0]['polygon']
    extract_figure(png_files[0], polygon)

### Document Intelligence with MS Word documents (docx)

Another sample document ..

In [32]:
path = r"sample_data/2_ai_facts.docx"
docx_result = analyze_document(path)
Markdown(docx_result['content'])

# AI Facts


## Fun Facts

Artificial Intelligence (AI) has evolved dramatically from its inception, leading to fascinating developments and applications that stretch the boundaries of what we once thought possible. One of the most engaging aspects of AI is its application in creative fields. For instance, AI has been used to compose music, generate unique pieces of art, and even write poetry, demonstrating its ability to learn and mimic human creativity. These applications have not only provided new tools for artists and creators but have also sparked debates about the nature of creativity and whether it is a uniquely human trait.

Another fun fact about AI is its ability to play and excel in complex games, a domain once believed to be the exclusive realm of human intelligence. AI systems like DeepMind's AlphaGo have defeated world champions in games like Go, which is known for its intricate strategy and depth. These achievements are not just about winning games; they represent significant advancements in AI's problem-solving and strategic planning capabilities. The algorithms developed for these purposes have broader applications, such as solving complex logistical problems and improving decision-making processes in business and science.


## AI Facts


<table>
<tr>
<th>Fact Category</th>
<th>Detail</th>
</tr>
<tr>
<td>Definition</td>
<td>AI, or Artificial Intelligence, refers to the simulation of human intelligence in machines that are programmed to think and learn like humans.</td>
</tr>
<tr>
<td>First AI Concept</td>
<td>The concept of artificial intelligence was first theorized by Alan Turing, a British mathematician, in 1950 through the Turing Test.</td>
</tr>
<tr>
<td>First AI Program</td>
<td>The first AI program was developed by Allen Newell and Herbert A. Simon in 1955, which was called the Logic Theorist.</td>
</tr>
<tr>
<td>Machine Learning</td>
<td>Machine learning is a subset of AI that involves the development of algorithms allowing computers to learn from and make decisions based on data.</td>
</tr>
<tr>
<td>Deep Learning</td>
<td>Deep learning is a subset of machine learning involving neural networks with many layers, enabling advanced pattern recognition.</td>
</tr>
<tr>
<td>AI in Healthcare</td>
<td>AI applications in healthcare include diagnostics, personalized medicine, and robot-assisted surgery.</td>
</tr>
<tr>
<td>AI in Autonomous Vehicles</td>
<td>AI enables autonomous vehicles to perceive their environment and make decisions, reducing the need for human intervention.</td>
</tr>
<tr>
<td>Natural Language Processing (NLP)</td>
<td>NLP is a field of AI focused on the interaction between computers and humans through natural language.</td>
</tr>
<tr>
<td>Ethics in AI</td>
<td>Ethical concerns in AI include privacy, bias, accountability, and the potential for job displacement.</td>
</tr>
<tr>
<td>AI in Finance</td>
<td>AI is used in finance for algorithmic trading, fraud detection, and customer service through chatbots.</td>
</tr>
<tr>
<td>Robotics</td>
<td>Robotics is a field related to AI, focusing on the design and manufacturing of robots that can perform tasks autonomously.</td>
</tr>
<tr>
<td>AI in Gaming</td>
<td>AI enhances gaming experiences by enabling more complex and realistic NPC behaviors and game environments.</td>
</tr>
<tr>
<td>AI in Education</td>
<td>AI can personalize learning experiences through adaptive learning systems and automate administrative tasks.</td>
</tr>
<tr>
<td>AI in Entertainment</td>
<td>AI is used in entertainment for content recommendation algorithms, music composition, and visual effects.</td>
</tr>
<tr>
<td>Quantum Computing and AI</td>
<td>Quantum computing has the potential to significantly increase the processing power available for AI tasks, leading to breakthroughs in complex problem-solving.</td>
</tr>
<tr>
<td>Bias in AI</td>
<td>AI systems can exhibit bias if they are trained on biased data sets, leading to unfair outcomes.</td>
</tr>
<tr>
<td>AI and Job Creation</td>
<td>While AI can automate tasks, it also creates new job opportunities in AI development, supervision, and maintenance.</td>
</tr>
<tr>
<td>AI in Agriculture</td>
<td>AI applications in agriculture include crop monitoring, predictive analysis for yield optimization, and automated machinery.</td>
</tr>
<tr>
<td>AI and Climate Change</td>
<td>AI can analyze large datasets to model climate change impacts and optimize energy consumption patterns.</td>
</tr>
<tr>
<td>AI Art and Creativity</td>
<td>AI is used to generate art, music, and literature, challenging traditional notions of creativity.</td>
</tr>
</table>


## Some More Fun Facts

AI has also made unexpected discoveries and contributions to various scientific fields. For instance, AI algorithms have identified new patterns in data that were previously overlooked by human researchers, leading to new scientific discoveries. In the realm of astronomy, AI has helped identify new exoplanets and galaxies by analyzing vast amounts of data from telescopes and space missions. Similarly, in biology, AI has accelerated the discovery of new molecules and drugs by predicting their structures and interactions more efficiently than traditional methods.

The relationship between AI and animals presents another intriguing aspect. Researchers have used AI to understand animal behavior and communication better. For example, AI has been employed to decode the complex language of dolphins and to track and predict the migration patterns of birds and other wildlife. These studies not only deepen our understanding of the natural world but also demonstrate AI's potential to bridge the communication gap between humans and other species. As AI continues to evolve, its applications expand into new and unexpected territories, promising to revolutionize our understanding of the world around us and beyond.


In [ ]:
print(docx_result['content'])

### Document Intelligence with PDF Documents

Notice the broken table over 3 pages, which gives 3 tables

In [ ]:
path = r"sample_data/2_ai_facts.pdf"
pdf_result = analyze_document(path)
Markdown(pdf_result['content'])

It seems that for the PDF, Document Intelligence did not correctly identify this as a single table, but rather as three separate tables.

In [ ]:
print(pdf_result['content'])

### Table Merging

Let's try to merge the tables using OpenAI GPT-4

In [ ]:
#### Let's try something "hacky"

if len(niche_pdf_result['content'].split('|\n')) > 0: ## This is a hacky way to check if there is a Markdown table in the text
    print('yes')


#### First Step

First try to establish the table boundaries

In [33]:
## Experiment with prompting, to see if broken tables can be "merged" based on LLM's output
## This is work in progress .. NOT YET COMPLETE


prompt = """
You are a Markdown expert whose objective is to check whether Markdown tables have been split into two or more tables because of page breaks or because of the OCR extraction process. You are designed to output JSON.

You are given the following Markdown text:
## START OF MARKDOWN TEXT
{text}
## END OF MARKDOWN TEXT

In the markdown text above, detect whether there are Markdown tables. If there are, you **MUST** then output the first row and the last row of each table. We define a Markdown table by having consecutive rows with no space between, with the each row separated from the next by '|\n'. Do not separate Markdown table semantically. 


JSON OUTPUT FORMAT:
You **MUST** output a JSON object with the following key-value pairs and following format:

{{
    "total_number_of_markdown_tables_located:": "the total number of Markdown tables located",,
    "table_first_and_last_rows_array":
    [
        {{
            "first_row": "The first row in Markdown table format. Make sure that the last row of the first table is outputted verbatim word-for-word, including any leading or trailing spaces, and any leading or trailing pipes.",
            "last_row": "The last row of the table in Markdown table format. Make sure that the first row of the second table is outputted verbatim word-for-word, including any leading or trailing spaces, and any leading or trailing pipes.",
        }}
    ]
}}
"""

p = prompt.format(text = niche_pdf_result['content'])
table_edges = ask_LLM_with_JSON(p, model_info=model_info)
print(table_edges)




Calling OpenAI APIs with 2 messages - Model: gpt-4t - Endpoint: https://admin-m78bg318-swedencentral.openai.azure.com/openai/

Messages: [{'role': 'system', 'content': 'You are a helpful assistant, who helps the user with their query. You are designed to output JSON.'}, {'role': 'user', 'content': '\nYou are a Markdown expert whose objective is to check whether Markdown tables have been split into two or more tables because of page breaks or because of the OCR extraction process. You are designed to output JSON.\n\nYou are given the following Markdown text:\n## START OF MARKDOWN TEXT\n<figure>\n\nClearAlpha®\nTechnologies\n\n</figure>\n\n\nNICHE PLUS MASTER FUND LTD\n\nSubscription Documents\n(FOR NON-U.S. INITIAL INVESTORS)\nRelating to Class S Shares\n\nInvestment Manager:\nClearAlpha Technologies LP\n500 West Putnam Avenue, Suite 400\nGreenwich, Connecticut 06830\nE-mail: investor.relations@clearalphatech.com\n\nAdministrator:\nHedgeServ (Cayman) Ltd.\n6th Floor SIX Cricket Square\

#### Second Step

Second, try to use the tables boundaries to determine whether the tables are split because of the pages, or OCR extraction, and if they are, try to merge

In [34]:

prompt = """
You are a Markdown expert whose objective is to check whether Markdown tables have been split into two or more tables because of page breaks or because of the OCR extraction process. You are designed to output JSON.

You are given the following Markdown text:
## START OF MARKDOWN TEXT
{text}
## END OF MARKDOWN TEXT

The below are the edges that define the start and end of each Markdown table. Use the first and last row mentioned in the "table_first_and_last_rows_array" as the definition of a Markdown table:
## START OF TABLE EDGES
{table_edges}
## END OF TABLE EDGES

In the markdown text above, detect whether there are Markdown tables. If there are, you **MUST** follow the Chain of Thought below:
    1. Locate every Markdown table in the text using the provided Table Edges, and write down the number of those tables in your scratchpad.
    2. Work on every two consecutive Markdown tables in a pairwise manner. For every pair of consecutive Markdown tables, you **MUST** check if they have any text between them. If the two tables are immediately consecutive, but there is text between them and this text is a footnote or a page number, you can safely ignore it, and mark the two tables as consecutive in your scratchpad. If, however, there is valid text between the two tables, then you **MUST** mark the two tables as not consecutive in your scratchpad.
    3. Write down the number of checks you have to perform. You will have to perform checks for consecutive tables pair-wise.

 After completing the above steps, you **MUST** then do the following for every two immediately consecutive Markdown table:
    A. If the separated Markdown tables are immediately consecutive, then check the headers and the data type of the columns of each table to estimate if the two tables originated from the same table but got split into two because of the page break, or because of the OCR extraction process.
    B. If you find that these two Markdown tables likely belong to the same original table, then output **EXACTLY** the full last row of the first table, and the first full row of the first table in Markdown table format. Also output the exact string of characters that exist between the two tables in the JSON output.
    C. Repeat the above steps for **ALL** immediately consecutive Markdown tables located in your scratchpad, to match the number of checks in your scratchpad.

**SUPER IMPORTANT**: We define a Markdown table by having consecutive rows with no space between, with the each row separated from the next by '|\n'. Do not separate Markdown table semantically. 


JSON OUTPUT FORMAT:
Remember that you **MUST** process every two immediately consecutive or consecutive Markdown tables. You **MUST** output a JSON object with the following key-value pairs and following format:

{{
    "total_number_of_markdown_tables_located:": "the total number of Markdown tables located",
    "num_of_tables_to_be_merged": "the number of tables to be merged",
    "tables_to_be_merged":
    [
        {{
            "first_table_last_row": "The last row of the first table in Markdown table format. Make sure that the last row of the first table is outputted verbatim word-for-word, including any leading or trailing spaces, and any leading or trailing pipes.",
            "second_table_first_row": "The first row of the second table in Markdown table format. Make sure that the first row of the second table is outputted verbatim word-for-word, including any leading or trailing spaces, and any leading or trailing pipes.",
            "dividing_string": "The exact string of characters that exist between the two tables. Make sure that the string is outputted verbatim word-for-word, including any leading or trailing spaces, and any leading or trailing pipes.",
        }}
    ]
}}

"""

p = prompt.format(text = niche_pdf_result['content'], table_edges=table_edges)
output = ask_LLM_with_JSON(p, model_info=model_info)
print(output)





Calling OpenAI APIs with 2 messages - Model: gpt-4t - Endpoint: https://admin-m78bg318-swedencentral.openai.azure.com/openai/

Messages: [{'role': 'system', 'content': 'You are a helpful assistant, who helps the user with their query. You are designed to output JSON.'}, {'role': 'user', 'content': '\nYou are a Markdown expert whose objective is to check whether Markdown tables have been split into two or more tables because of page breaks or because of the OCR extraction process. You are designed to output JSON.\n\nYou are given the following Markdown text:\n## START OF MARKDOWN TEXT\n<figure>\n\nClearAlpha®\nTechnologies\n\n</figure>\n\n\nNICHE PLUS MASTER FUND LTD\n\nSubscription Documents\n(FOR NON-U.S. INITIAL INVESTORS)\nRelating to Class S Shares\n\nInvestment Manager:\nClearAlpha Technologies LP\n500 West Putnam Avenue, Suite 400\nGreenwich, Connecticut 06830\nE-mail: investor.relations@clearalphatech.com\n\nAdministrator:\nHedgeServ (Cayman) Ltd.\n6th Floor SIX Cricket Square\

In [ ]:
import json
import copy


## Let's try to merge the tables
findings = json.loads(output)
pdf_content = copy.deepcopy(niche_pdf_result['content'])


for table in findings['tables_to_be_merged']:
    first = table['first_table_last_row']
    second = table['second_table_first_row']

    print("Row in first table found: ", first in niche_pdf_result['content'])
    print("Row in last table found: ", second in niche_pdf_result['content'])

    for table in findings['tables_to_be_merged']:
        first_table_last_row = table['first_table_last_row']
        second_table_first_row = table['second_table_first_row']

        first_part = pdf_content.split(first_table_last_row)[0]
        second_part = pdf_content.split(second_table_first_row)[1]

        pdf_content = first_part + first_table_last_row + '\n' + second_table_first_row + second_part


Markdown(pdf_content)



In [ ]:
print(pdf_content)

### Using Regex to detect table boundaries

Maybe an easier way is to use Regex to detect table boundaries, and then post-process to the correct format using GPT-4 if the table is not big. 

In [ ]:
## Regex will extract all 3 tables as one contiguous table

tables = extract_markdown_table(niche_pdf_result['content'])

print(len(tables))
Markdown(tables[0][0])

This time we artificially separate the same tables with some text. RegEx would detect 2 tables instead of one.

In [ ]:
cc = """
# AI Facts

|||
| - | - |
| Fact Category | Detail |
| Definition | AI, or Artificial Intelligence, refers to the simulation of human intelligence in machines that are programmed to think and learn like humans. |
| First AI Concept | The concept of artificial intelligence was first theorized by Alan Turing, a British mathematician, in 1950 through the Turing Test. |
| First AI Program | The first AI program was developed by Allen Newell and Herbert A. Simon in 1955, which was called the Logic Theorist. |
| Machine Learning | Machine learning is a subset of AI that involves the development of algorithms allowing computers to learn from and make decisions based on data. |

Another fun fact about AI is its ability to play and excel in complex games, a domain once believed to be the exclusive realm of human intelligence. AI systems like DeepMind's AlphaGo have defeated world champions in games like Go, which is known for its intricate strategy and depth. These achievements are not just about winning games; they represent significant advancements in AI's problem-solving and strategic planning capabilities. The algorithms developed for these purposes have broader applications, such as solving complex logistical problems and improving decision- making processes in business and science.

|||
| - | - |
| Deep Learning | Deep learning is a subset of machine learning involving neural networks with many layers, enabling advanced pattern recognition. |
| AI in Healthcare | AI applications in healthcare include diagnostics, personalized medicine, and robot-assisted surgery. |
| AI in Autonomous Vehicles | AI enables autonomous vehicles to perceive their environment and make decisions, reducing the need for human intervention. |
| Natural Language Processing (NLP) | NLP is a field of AI focused on the interaction between computers and humans through natural language. |
| Ethics in AI | Ethical concerns in AI include privacy, bias, accountability, and the potential for job displacement. |
| AI in Finance | AI is used in finance for algorithmic trading, fraud detection, and customer service through chatbots. |
| Robotics | Robotics is a field related to AI, focusing on the design and manufacturing of robots that can perform tasks autonomously. |
| AI in Gaming | AI enhances gaming experiences by enabling more complex and realistic NPC behaviors and game environments. |
| AI in Education | AI can personalize learning experiences through adaptive learning systems and automate administrative tasks. |
| AI in Entertainment | AI is used in entertainment for content recommendation algorithms, music composition, and visual effects. |
| Quantum Computing and AI | Quantum computing has the potential to significantly increase the processing power available for AI tasks, leading to breakthroughs in complex problem-solving. |
| Bias in AI | AI systems can exhibit bias if they are trained on biased data sets, leading to unfair outcomes. |

"""


tables = extract_markdown_table(cc)

print(len(tables))
Markdown(tables[0][0])


In [ ]:
#### Change prompt and provide an example

In [ ]:
## Experiment with prompting, to see if broken tables can be "merged" based on LLM's output
## This is work in progress .. NOT YET COMPLETE

prompt = """
You are a Markdown expert whose objective is to check whether Markdown tables have been split into two or more tables because of page breaks or because of the OCR extraction process. You are designed to output JSON.

You are given the following Markdown text:
## START OF MARKDOWN TEXT
{text}
## END OF MARKDOWN TEXT

In the markdown text above, detect whether there are Markdown tables. If table is spanning across pages, you **MUST** combine table chunks from consecutive pages and create single table **BEFORE** output to JSON.

## EXAMPLE
Here is example of table that spans across pages:

|||
| - | - |
| Column1 | Column2 | ColumnN |
| Row1 Column1 value | Row1 Column2 value | Row1 ColumnN value |
| Row2 Column1 value | Row2 Column2 value | Row2 ColumnN value |

|||
| - | - |
| RowX Column1 value | RowX Column2 value | RowX ColumnN value |
| RowY Column1 value | RowY Column2 value | RowY ColumnN value |

## COMBINED TABLE
Here result of combining table chunks from consecutive pages. First row is always the header row.

| Column1 | Column2 | ColumnN |
| Row1 Column1 value | Row1 Column2 value | Row1 ColumnN value |
| Row2 Column1 value | Row2 Column2 value | Row2 ColumnN value |
| RowX Column1 value | RowX Column2 value | RowX ColumnN value |
| RowY Column1 value | RowY Column2 value | RowY ColumnN value |

## JSON OUTPUT FORMAT:
You **MUST** output a JSON object with the following key-value pairs and following format. Do **NOT* provide any other comments or unnecessary information in the JSON output:

{{
    "Column1 Header":
        [
                "Row1 value",
                "Row2 value",
                ...,
                "RowN value"
            }}
        ],
    "Column2 Header":
        [
                "Row1 value",
                "Row2 value",
                ...,
                "RowN value"
            }}
        ],
    ...,
    "ColumnN Header":
        [
                "Row1 value",
                "Row2 value",
                ...,
                "RowN value"
            }}
        ]
}}
"""

p = prompt.format(text = pdf_result['content'])
table_edges = ask_LLM_with_JSON(p, model_info=model_info)
print(table_edges)

In [ ]:
import pandas as pd
import json

# Parse the JSON string
data = json.loads(table_edges)

# Create DataFrame
df = pd.DataFrame(data)

# Display the DataFrame
display(df)


#### Lets try with different PDF file

In [ ]:
path = r"sample_data/hdgdemo/Gladius_Capital_Fund LP_117.pdf"
pdf_result = analyze_document(path)
Markdown(pdf_result['content'])

In [41]:
## Experiment with prompting, to see if broken tables can be "merged" based on LLM's output
## This is work in progress .. NOT YET COMPLETE

prompt = """
You are a Markdown expert whose objective is to check whether Markdown tables have been split into two or more tables because of page breaks or because of the OCR extraction process. You are designed to output JSON.

You are given the following Markdown text:
## START OF MARKDOWN TEXT
{text}
## END OF MARKDOWN TEXT

In the markdown text above, detect whether there are Markdown tables. If table is spanning across pages, you **MUST** combine table chunks from consecutive pages and create single table **BEFORE** output to JSON.

## EXAMPLE
Here is example of table that spans across pages:

|||
| - | - |
| Column1 | Column2 | ColumnN |
| Row1 Column1 value | Row1 Column2 value | Row1 ColumnN value |
| Row2 Column1 value | Row2 Column2 value | Row2 ColumnN value |

|||
| - | - |
| RowX Column1 value | RowX Column2 value | RowX ColumnN value |
| RowY Column1 value | RowY Column2 value | RowY ColumnN value |

## COMBINED TABLE
Here result of combining table chunks from consecutive pages. First row is always the header row.

| Column1 | Column2 | ColumnN |
| Row1 Column1 value | Row1 Column2 value | Row1 ColumnN value |
| Row2 Column1 value | Row2 Column2 value | Row2 ColumnN value |
| RowX Column1 value | RowX Column2 value | RowX ColumnN value |
| RowY Column1 value | RowY Column2 value | RowY ColumnN value |

## JSON OUTPUT FORMAT:
You **MUST** output a JSON object with the following key-value pairs and following format. Do **NOT* provide any other comments or unnecessary information in the JSON output:

{{
    "Column1 Header":
        [
                "Row1 value",
                "Row2 value",
                ...,
                "RowN value"
            }}
        ],
    "Column2 Header":
        [
                "Row1 value",
                "Row2 value",
                ...,
                "RowN value"
            }}
        ],
    ...,
    "ColumnN Header":
        [
                "Row1 value",
                "Row2 value",
                ...,
                "RowN value"
            }}
        ]
}}
"""

p = prompt.format(text = pdf_result['content'])
table_edges = ask_LLM_with_JSON(p, model_info=model_info)
print(table_edges)


Calling OpenAI APIs with 2 messages - Model: gpt-4t - Endpoint: https://admin-m78bg318-swedencentral.openai.azure.com/openai/

Messages: [{'role': 'system', 'content': 'You are a helpful assistant, who helps the user with their query. You are designed to output JSON.'}, {'role': 'user', 'content': '\nYou are a Markdown expert whose objective is to check whether Markdown tables have been split into two or more tables because of page breaks or because of the OCR extraction process. You are designed to output JSON.\n\nYou are given the following Markdown text:\n## START OF MARKDOWN TEXT\n<!-- PageHeader="Copy No. 117" -->\n\n\n# GLADIUS CAPITAL FUND LP\n\n\n## INSTRUCTIONS TO SUBSCRIPTION AGREEMENT\n\nAny person desiring to become a limited partner of Gladius Capital Fund LP (the\n"Partnership") should complete and execute:\n\n(a) one (1) copy of the attached Subscription Agreement (the "Agreement"), offering to\nmake a capital contribution in the amount set forth below its name at the e

In [39]:
import pandas as pd
import json

# Parse the JSON string
data = json.loads(table_edges)

# Create DataFrame
df = pd.DataFrame(data)

# Display the DataFrame
display(df)


Accredited Investor Status  \
☐  [(i) Individual - Income Test. An individual w...   

                          Qualified Purchaser Status  
☐  [(i) Individual. An individual who owns not le...

In [45]:
## Experiment with prompting, to see if relevant data can be extracted and provided in json output
## This is work in progress .. NOT YET COMPLETE

prompt = """
You are a Entity Extraction and Markdown expert whose objective is to check whether Markdown text has corresponding entities and if so you are to extract as key value pair. You are designed to output JSON.

You are given the following Markdown text:
## START OF MARKDOWN TEXT
{text}
## END OF MARKDOWN TEXT

In the markdown text above, detect whether there are entities fields that are mentioned in below example. If the markdown text has information about entity field, you **MUST** combine that field information as key value pair and create single data set **BEFORE** output to JSON.

## EXAMPLE
Here is example of entities that you are looking for:

internal_id,	external_id,	row_linking_id,	master_account_type,	entity_individual,	first_name,	middle_name,	last_name,	legal_entity_type,	jurisdiction_of_org,	jurisdiction_state,	principal_place_of_business,	principal_state,	private_equity_master,	pep,	erisa_treatment,	modified_date,	modified_by,	w8_doc_received,	w8_doc_last_received_date,	w8_tax_classification,	w8_other_tax_classification,	w9_doc_received,	w9_doc_last_received_date,	w9_tax_classification,	w9_other_tax_classification,	tax_residence_1,	tax_residence_state_1,	tax_id_1,	tax_residence_2,	tax_residence_state_2,	tax_id_2,	tax_residence_3,	tax_residence_state_3,	tax_id_3,	tax_residence_4,	tax_residence_state_4,	tax_id_4,	disregarded_entity,	disregarded_entity_name,	disregarded_entity_ein_ssn,	disregarded_entity_address,	address_internal_id,	address_external_id,	attn_to,	company,	address_1,	address_2,	address_3,	city,	state,	zip,	country,	work_phone,	home_phone,	cell_phone,	fax,	email,	email_cc,	email_bcc


## JSON OUTPUT FORMAT:
You **MUST** output a JSON object with the following key-value pairs and following format. Do **NOT* provide any other comments or unnecessary information in the JSON output:

{{
"internal_id": " ",
"external_id": " ",
"row_linking_id": " ",
"master_account_type": " ",
"entity_individual": " ",
"first_name": " ",
"middle_name": " ",
"last_name": " ",
"legal_entity_type": " ",
"jurisdiction_of_org": " ",
"jurisdiction_state": " ",
"principal_place_of_business": " ",
"principal_state": " ",
"private_equity_master": " ",
"pep": " ",
"erisa_treatment": " ",
"modified_date": " ",
"modified_by": " ",
"w8_doc_received": " ",
"w8_doc_last_received_date": " ",
"w8_tax_classification": " ",
"w8_other_tax_classification": " ",
"w9_doc_received": " ",
"w9_doc_last_received_date": " ",
"w9_tax_classification": " ",
"w9_other_tax_classification": " ",
"tax_residence_1": " ",
"tax_residence_state_1": " ",
"tax_id_1": " ",
"tax_residence_2": " ",
"tax_residence_state_2": " ",
"tax_id_2": " ",
"tax_residence_3": " ",
"tax_residence_state_3": " ",
"tax_id_3": " ",
"tax_residence_4": " ",
"tax_residence_state_4": " ",
"tax_id_4": " ",
"disregarded_entity": " ",
"disregarded_entity_name": " ",
"disregarded_entity_ein_ssn": " ",
"disregarded_entity_address": " ",
"address_internal_id": " ",
"address_external_id": " ",
"attn_to": " ",
"company": " ",
"address_1": " ",
"address_2": " ",
"address_3": " ",
"city": " ",
"state": " ",
"zip": " ",
"country": " ",
"work_phone": " ",
"home_phone": " ",
"cell_phone": " ",
"fax": " ",
"email": " ",
"email_cc": " ",
"email_bcc": " "


    }}
"""
p = prompt.format(text = pdf_result['content'])
gladis_master_data = ask_LLM_with_JSON(p, model_info=model_info)
print(gladis_master_data)





Calling OpenAI APIs with 2 messages - Model: gpt-4t - Endpoint: https://admin-m78bg318-swedencentral.openai.azure.com/openai/

Messages: [{'role': 'system', 'content': 'You are a helpful assistant, who helps the user with their query. You are designed to output JSON.'}, {'role': 'user', 'content': '\nYou are a Entity Extraction and Markdown expert whose objective is to check whether Markdown text has corresponding entities and if so you are to extract as key value pair. You are designed to output JSON.\n\nYou are given the following Markdown text:\n## START OF MARKDOWN TEXT\n<!-- PageHeader="Copy No. 117" -->\n\n\n# GLADIUS CAPITAL FUND LP\n\n\n## INSTRUCTIONS TO SUBSCRIPTION AGREEMENT\n\nAny person desiring to become a limited partner of Gladius Capital Fund LP (the\n"Partnership") should complete and execute:\n\n(a) one (1) copy of the attached Subscription Agreement (the "Agreement"), offering to\nmake a capital contribution in the amount set forth below its name at the end of this

### Let us extract now the Transaction information

In [56]:
## Experiment with prompting, to see if relevant data can be extracted and provided in json output
## This is work in progress .. NOT YET COMPLETE

prompt = """
You are a Entity Extraction and Markdown expert whose objective is to check whether Markdown text has corresponding entities and if so you are to extract as key value pair. You are designed to output JSON.

You are given the following Markdown text:
## START OF MARKDOWN TEXT
{text}
## END OF MARKDOWN TEXT

In the markdown text above, detect whether there are entities fields that are mentioned in below example. If the markdown text has information about entity field, you **MUST** combine that field information from Content text as key value pair and create single data set **BEFORE** output to JSON.

## EXAMPLE
Here is example of entities that you are looking for:

action,	fundCode,	fundInternalId,	transactionDate,	transactionInternalId,	transactionExternalId,	transactionType,	investorInternalId,	investorExternalId,	investorName,	className,	fundClassInternalId,	allocationMethod,	seriesPiInternalId,	seriesPiExternalId,	seriesPiName,	lotInternalId,	lotExternalId,	lotNumber,	currency,	entryType,	capitalPct,	shares,	amount,	transferToInvestorInternalId,	transferToInvestorExternalId,	transferToInvestorName,	transferToPartnerInternalId,	transferToPartnerExternalId,	transferToPartnerName,	exchangeToClassName,	exchangeToSeriesPIInternalId,	exchangeToSeriesPIExternalId,	exchangeToSeriesPIName,	exchangeAtNetGrossCapital,	externalEQIssueOriginalLotId,	crystallizationMethod,	investorGroup1


## JSON OUTPUT FORMAT:
You **MUST** output a JSON object with the following key-value pairs and following format. Do **NOT* provide any other comments or unnecessary information in the JSON output:

{{

"action": " ",
"fundCode": " ",
"fundInternalId": " ",
"transactionDate": " ",
"transactionInternalId": " ",
"transactionExternalId": " ",
"transactionType": " ",
"investorInternalId": " ",
"investorExternalId": " ",
"investorName": " ",
"className": " ",
"fundClassInternalId": " ",
"allocationMethod": " ",
"seriesPiInternalId": " ",
"seriesPiExternalId": " ",
"seriesPiName": " ",
"lotInternalId": " ",
"lotExternalId": " ",
"lotNumber": " ",
"currency for capital contribution": " ",
"entryType": " ",
"capitalPct": " ",
"shares": " ",
"Capital Contribution amount": " ",
"transferToInvestorInternalId": " ",
"transferToInvestorExternalId": " ",
"transferToInvestorName": " ",
"transferToPartnerInternalId": " ",
"transferToPartnerExternalId": " ",
"transferToPartnerName": " ",
"exchangeToClassName": " ",
"exchangeToSeriesPIInternalId": " ",
"exchangeToSeriesPIExternalId": " ",
"exchangeToSeriesPIName": " ",
"exchangeAtNetGrossCapital": " ",
"externalEQIssueOriginalLotId": " ",
"crystallizationMethod": " ",
"investorGroup1": " "
    }}
"""
p = prompt.format(text = pdf_result['content'])
##print(p)
gladis_txn_data = ask_LLM_with_JSON(p, model_info=model_info)
print(gladis_txn_data)



Calling OpenAI APIs with 2 messages - Model: gpt-4t - Endpoint: https://admin-m78bg318-swedencentral.openai.azure.com/openai/

Messages: [{'role': 'system', 'content': 'You are a helpful assistant, who helps the user with their query. You are designed to output JSON.'}, {'role': 'user', 'content': '\nYou are a Entity Extraction and Markdown expert whose objective is to check whether Markdown text has corresponding entities and if so you are to extract as key value pair. You are designed to output JSON.\n\nYou are given the following Markdown text:\n## START OF MARKDOWN TEXT\n<!-- PageHeader="Copy No. 117" -->\n\n\n# GLADIUS CAPITAL FUND LP\n\n\n## INSTRUCTIONS TO SUBSCRIPTION AGREEMENT\n\nAny person desiring to become a limited partner of Gladius Capital Fund LP (the\n"Partnership") should complete and execute:\n\n(a) one (1) copy of the attached Subscription Agreement (the "Agreement"), offering to\nmake a capital contribution in the amount set forth below its name at the end of this